In [ ]:
# Copyright 2020 IITK EE604A Image Processing. All Rights Reserved.
# 
# Licensed under the MIT License. Use and/or modification of this code outside of EE604 must reference:
#
# © IITK EE604A Image Processing 
# https://github.com/ee604/ee604_assignments
#
# Author: Shashi Kant Gupta, Chiranjeev Prachand and Prof K. S. Venkatesh, Department of Electrical Engineering, IIT Kanpur

# Task 4 (Bonus Question): Video Stabilization

For this bonus question, you have to search and find a suitable solution to stabilize the provided shaky video. You are free to follow any approach/method or python modules to do this. Unless until following conditions satisfy:

* Any modules which you use should not be a direct implementation.
* By "stabilization," we do not mean a perfect solution. But it should be satisfactorily better than the original video.

In [3]:
%%bash
pip install git+https://github.com/ee604/ee604_plugins
pip install git+https://github.com/shashikg/google_colab_plugins
mkdir output

  Cloning https://github.com/ee604/ee604_plugins to /tmp/pip-req-build-jzc_nkl7
  Created wheel for ee604-plugins: filename=ee604_plugins-0.4.2-cp36-none-any.whl size=2457 sha256=6ceb532536bc4c1f8e00a300b6af6760ddf71052d48ece8c2142f9df85320f93
  Stored in directory: /tmp/pip-ephem-wheel-cache-6f0gf2jz/wheels/34/a8/1d/ae3b7d209ecde89b4800a47ec55a61e7503bb9548bbb975806
Successfully built ee604-plugins
  Cloning https://github.com/shashikg/google_colab_plugins to /tmp/pip-req-build-ojfo9b6d
  Created wheel for google-colab-plugins: filename=google_colab_plugins-0.1-cp36-none-any.whl size=3074 sha256=3ee208b4088c74f14a7a5e08f138bba2caab34da513f576b85399295a1478e30
  Stored in directory: /tmp/pip-ephem-wheel-cache-jc7z0l2v/wheels/0d/7a/c0/f08e26849983b61cab0600b42d2547a3a963f611f738877eff
Successfully built google-colab-plugins


  Running command git clone -q https://github.com/ee604/ee604_plugins /tmp/pip-req-build-jzc_nkl7
  Running command git clone -q https://github.com/shashikg/google_colab_plugins /tmp/pip-req-build-ojfo9b6d


In [4]:
# Importing required libraries

import cv2
import numpy as np
import matplotlib.pyplot as plt
!pip install scikit-video
!pip install google_colab_plugins

from IPython.display import display
from PIL import Image
from google_colab_plugins import playVideo
from skvideo.io import FFmpegWriter as VideoWriter
from ee604_plugins import download_dataset

download_dataset(assignment_no=4, task_no=4)

     |████████████████████████████████| 2.3MB 4.2MB/s 
Download Complete!


In [5]:
orig_video_dir = "data/shaky_video.mp4"
stab_video_dir = "output/stab_video.mp4"

print("Original shaky video")
playVideo(filename=orig_video_dir)

Original shaky video


In [6]:
def movingAverage(c, r): 
  kernel = np.ones(2*r + 1)/(2*r + 1) 
  c_pad = np.lib.pad(c, (r, r), 'edge') 
  out = np.convolve(c_pad, kernel, mode='same') 
  out = out[r:-r]
  return out 

def smooth(traj): 
  out = np.copy(traj) 
  for i in range(3):
    out[:,i] = movingAverage(traj[:,i], r=SMOOTHING_RADIUS)
  return out

def fixBorder(window):
  x = window.shape
  #scaling the image by 4% without moving the center
  rot_mat = cv2.getRotationMatrix2D((x[1]/2, x[0]/2), 0, 1.04)
  window = cv2.warpAffine(window, rot_mat, (x[1], x[0]))
  return window

In [7]:
SMOOTHING_RADIUS=50 
cap = cv2.VideoCapture(orig_video_dir) 
n_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT)) 
fps = int(n_frames/21)

w = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH)) 
h = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

out = VideoWriter(stab_video_dir, inputdict={'-r': str(fps)}, outputdict={'-r': str(fps)})

In [8]:
_, prev = cap.read() 
prev_gray = cv2.cvtColor(prev, cv2.COLOR_BGR2GRAY) 
transforms = np.zeros((n_frames-1, 3), np.float32) 

for i in range(n_frames-2):
  prev_pts = cv2.goodFeaturesToTrack(prev_gray, maxCorners=200, qualityLevel=0.01, minDistance=30, blockSize=3)
  success, curr = cap.read() 
  if not success: 
    break 
  curr_gray = cv2.cvtColor(curr, cv2.COLOR_BGR2GRAY) 
  curr_pts, status, err = cv2.calcOpticalFlowPyrLK(prev_gray, curr_gray, prev_pts, None) 
  assert prev_pts.shape == curr_pts.shape 
  
  #Filtering only valid points 
  idx = np.where(status==1)[0]
  prev_pts = prev_pts[idx]
  curr_pts = curr_pts[idx]

  [m, inliers] =cv2.estimateAffinePartial2D	(prev_pts,curr_pts,method =cv2.RANSAC,maxIters = 2000,confidence = 0.99,refineIters = 10) 
  dx = m[0,2]
  dy = m[1,2]
  da = np.arctan2(m[1,0], m[0,0])
  transforms[i] = [dx,dy,da]
  
  prev_gray = curr_gray

trajectory = np.cumsum(transforms, axis=0) 
smoothed_trajectory = smooth(trajectory) 
difference = smoothed_trajectory - trajectory
transforms_smooth = transforms + difference

cap.set(cv2.CAP_PROP_POS_FRAMES, 0) 

for i in range(n_frames-2):
  success, frame = cap.read() 
  if not success:
    break
  dx = transforms_smooth[i,0]
  dy = transforms_smooth[i,1]
  da = transforms_smooth[i,2]

  m = np.zeros((2,3), np.float32)
  m[0,0] = np.cos(da)
  m[0,1] = -np.sin(da)
  m[1,0] = np.sin(da)
  m[1,1] = np.cos(da)
  m[0,2] = dx
  m[1,2] = dy

  frame_stabilized = cv2.warpAffine(frame, m, (w,h))
  frame_stabilized = fixBorder(frame_stabilized) 
  out.writeFrame(frame_stabilized)

out.close()

In [9]:
print("Stabilized Video. Kindly don't run this code in Firefox/Safari, as it turns out maybe Firfox or Safari doesn't support .mp4 playback formats in google colab. Use Google Chrome/Internet Explorer")
playVideo(filename=stab_video_dir) 

Stabilized Video. Kindly don't run this code in Firefox/Safari, as it turns out maybe Firfox or Safari doesn't support .mp4 playback formats in google colab. Use Google Chrome/Internet Explorer
